# CAI Lab Session 4: Implementing search in the vector space model

In this session you will:

- Continue to work with the `arxiv` repository from last session
- Learn how to do atomic, conjunctive and disjunctive search with ElasticSearch
- Build an inverted index for the `arxiv` repository from last session (should fit in main memory)
- Implement search in the vector space model and compare it with ElasticSearch built-in search mechanism
- Compare different implementations of search

## 1. Built-in search in ElasticSearch

ElasticSearch provides a search mechanism to make queries against a database. 
In the next code snippet you can find examples on how to do this with an atomic query (single term)
and with conjunctive and disjunctive queries.

In [2]:
from elasticsearch import Elasticsearch
from elasticsearch_dsl import Search
from elasticsearch_dsl.query import Q


client = Elasticsearch("http://localhost:9200", request_timeout=1000)
s = Search(using=client, index='arxiv')

## atomic query
q = Q('query_string',query='computer')  # Feel free to change the word

s = s.query(q)
response = s[:5].execute()
for r in response:  # only returns a specific number of results
    print('ID= %s SCORE=%s' % (r.meta.id,  r.meta.score))
    print('PATH= %s' % r.path)
    print('TEXT: %s' % r.text[:90])
    print()

ID= mlNkL4sBF4_-Pm_zvsNN SCORE=3.2082987
PATH= ../../arxiv\cs.updates.on.arXiv.org/002772
TEXT: Limit computable functions can be characterized by Turing jumps on the input side or limit

ID= clRkL4sBF4_-Pm_z6BJ_ SCORE=3.2082987
PATH= ../../arxiv\math.updates.on.arXiv.org/001904
TEXT: Limit computable functions can be characterized by Turing jumps on the input side or limit

ID= GlNkL4sBF4_-Pm_zxtUl SCORE=3.1941829
PATH= ../../arxiv\cs.updates.on.arXiv.org/007252
TEXT: We study scheduling of computation tasks across $n$ workers in a large scale distributed l

ID= DlRkL4sBF4_-Pm_z6xri SCORE=3.1941829
PATH= ../../arxiv\math.updates.on.arXiv.org/003852
TEXT: We study scheduling of computation tasks across $n$ workers in a large scale distributed l

ID= KFNkL4sBF4_-Pm_zx9YE SCORE=3.1520977
PATH= ../../arxiv\cs.updates.on.arXiv.org/007522
TEXT: Grid Computing is an idea of a new kind of network technology in which research work in pr



In [2]:
## conjunctive query

client = Elasticsearch("http://localhost:9200", request_timeout=1000)
s = Search(using=client, index='arxiv')

q = Q('query_string',query='computer') & Q('query_string',query='magic')

s = s.query(q)
response = s[0:5].execute()
for r in response:  # only returns a specific number of results
    print(f'ID= {r.meta.id} SCORE={r.meta.score}')
    print(f'PATH= {r.path}')
    print(f'TEXT: {r.text[:90]}')
    print()

ID= 1edDGosBAcLkfcUZTnGi SCORE=15.135108
PATH= /tmp/arxiv/quant-ph.updates.on.arXiv.org/000677
TEXT: We give a new algorithm for computing the robustness of magic - a measure of the utility o

ID= c-dDGosBAcLkfcUZT3RR SCORE=15.135108
PATH= /tmp/arxiv/quant-ph.updates.on.arXiv.org/000650
TEXT: We give a new algorithm for computing the robustness of magic - a measure of the utility o

ID= wOdDGosBAcLkfcUZTW_k SCORE=12.778042
PATH= /tmp/arxiv/quant-ph.updates.on.arXiv.org/001652
TEXT: A defining feature in the field of quantum computing is the potential of a quantum device 

ID= QudDGosBAcLkfcUZbeou SCORE=11.47281
PATH= /tmp/arxiv/cond-mat.updates.on.arXiv.org/000521
TEXT: Smale's 7-th problem concerns N-point configurations on the 2-dim sphere which minimize th

ID= TehDGosBAcLkfcUZgUnR SCORE=11.47281
PATH= /tmp/arxiv/math.updates.on.arXiv.org/000731
TEXT: Smale's 7-th problem concerns N-point configurations on the 2-dim sphere which minimize th



In [3]:
## disjunctive query

client = Elasticsearch("http://localhost:9200", request_timeout=1000)
s = Search(using=client, index='arxiv')

q = Q('query_string',query='computer') | Q('query_string',query='magic')

s = s.query(q)
response = s[0:5].execute()
for r in response:  # only returns a specific number of results
    print(f'ID= {r.meta.id} SCORE={r.meta.score}')
    print(f'PATH= {r.path}')
    print(f'TEXT: {r.text[:90]}')
    print()

ID= iFRkL4sBF4_-Pm_z_0ai SCORE=14.512409
PATH= ../../arxiv\quant-ph.updates.on.arXiv.org/000650
TEXT: We give a new algorithm for computing the robustness of magic - a measure of the utility o

ID= o1RkL4sBF4_-Pm_z_0ai SCORE=14.512409
PATH= ../../arxiv\quant-ph.updates.on.arXiv.org/000677
TEXT: We give a new algorithm for computing the robustness of magic - a measure of the utility o

ID= KVNkL4sBF4_-Pm_ztrEM SCORE=12.0883665
PATH= ../../arxiv\cond-mat.updates.on.arXiv.org/003482
TEXT: When two monolayers of graphene are stacked with a small relative twist angle, the resulti

ID= ClRkL4sBF4_-Pm_z4QbH SCORE=11.981175
PATH= ../../arxiv\hep-th.updates.on.arXiv.org/000265
TEXT: We introduce the extended Freudenthal-Rosenfeld-Tits magic square based on six algebras: t

ID= vVRkL4sBF4_-Pm_z5g5U SCORE=11.981175
PATH= ../../arxiv\math.updates.on.arXiv.org/000955
TEXT: We introduce the extended Freudenthal-Rosenfeld-Tits magic square based on six algebras: t



## 2. Excruciatingly slow search

In class we have presented a _slow_ version of search that, given a search query $q$, loops over every document in the database
computing the cosine similarity between document and query. Once this is done, it sorts documents by their similarity w.r.t. $q$ and returns the top $r$
scoring ones. 

```
1. for each d in D:
    sim(d,q) = 0
    get vector representing d
    for each w in q:
        sim(d,q) += tf(d,w) * idf(w)
    normalize sim(d,q) by |d|*|q|
2. sort results by similarity
3. return top r docs
```

A possible implementation can be found below. 

__Remark:__ _It should be important to note that there are certain elements in the implementation below that refer to my own
implementation, and that you should adapt to your own; in particular, the line_

```    weights = dict(normalize(tf_idf(s['_id'])))   # gets weights as a python dict of term -> weight ```

_obtains tf-idf weights through calling a function `tf_idf` that I have implemented that, given a docid, returns a list of pairs (term, weight); and `normalize` takes such a list a normalizes weights so that the corresponding vector has length 1. 
Obviously, you should adapt the code to your own implementations from previous sessions._


In [ ]:
!pip

In [5]:
from elasticsearch.helpers import scan
from pprint import pprint
from elasticsearch import Elasticsearch
import tqdm
import numpy as np

# get tf-idf vector from doc (internal) id
def tf_idf(doc_id):
    # does nothing, adapt to your needs
    return []

# normalizes weights so that resulting vec has length 1
def normalize(l1):
    # does nothing, adapt to your needs
    return l1

client = Elasticsearch("http://localhost:9200", request_timeout=1000)

r = 10  # only return r top docs
query = 'computer magic'
sims = dict()

l2query  = np.sqrt(len(query.split()))  # l2 of query assuming 0-1 vector representation

# get nr. of docs; just for the progress bar
ndocs = int(client.cat.count(index='arxiv', format = "json")[0]['count'])  # D

# scan through docs, compute cosine sim between query and each doc
for s in tqdm.tqdm(scan(client, index='arxiv', query={"query" : {"match_all": {}}}), total=ndocs):
    docid = s['_source']['path']   # use path as id
    
    sims[docid] = 0.0
    weights = dict(normalize(tf_idf(s['_id'])))

    print(docid, s['_id'])

    for w in query.split():  # gets terms as a list
        if w in weights:    # probably need to do something fancier to make sure that word is in vocabulary etc.
            sims[docid] += weights[w]   # accumulates if w in current doc

  2%|▏         | 1001/58102 [00:00<00:18, 3076.17it/s]

../../arxiv\astro-ph.updates.on.arXiv.org/000000 DlNkL4sBF4_-Pm_zhGg8
../../arxiv\astro-ph.updates.on.arXiv.org/000001 D1NkL4sBF4_-Pm_zhGhD
../../arxiv\astro-ph.updates.on.arXiv.org/000002 EFNkL4sBF4_-Pm_zhGhD
../../arxiv\astro-ph.updates.on.arXiv.org/000003 EVNkL4sBF4_-Pm_zhGhE
../../arxiv\astro-ph.updates.on.arXiv.org/000004 ElNkL4sBF4_-Pm_zhGhE
../../arxiv\astro-ph.updates.on.arXiv.org/000005 E1NkL4sBF4_-Pm_zhGhE
../../arxiv\astro-ph.updates.on.arXiv.org/000006 FFNkL4sBF4_-Pm_zhGhE
../../arxiv\astro-ph.updates.on.arXiv.org/000007 FVNkL4sBF4_-Pm_zhGhE
../../arxiv\astro-ph.updates.on.arXiv.org/000008 FlNkL4sBF4_-Pm_zhGhE
../../arxiv\astro-ph.updates.on.arXiv.org/000009 F1NkL4sBF4_-Pm_zhGhE
../../arxiv\astro-ph.updates.on.arXiv.org/000010 GFNkL4sBF4_-Pm_zhGhE
../../arxiv\astro-ph.updates.on.arXiv.org/000011 GVNkL4sBF4_-Pm_zhGhE
../../arxiv\astro-ph.updates.on.arXiv.org/000012 GlNkL4sBF4_-Pm_zhGhE
../../arxiv\astro-ph.updates.on.arXiv.org/000013 G1NkL4sBF4_-Pm_zhGhE
../../arxiv\astro-ph

  3%|▎         | 2001/58102 [00:00<00:16, 3460.24it/s]

../../arxiv\astro-ph.updates.on.arXiv.org/001001 91NkL4sBF4_-Pm_zjGsE
../../arxiv\astro-ph.updates.on.arXiv.org/001002 -FNkL4sBF4_-Pm_zjGsE
../../arxiv\astro-ph.updates.on.arXiv.org/001003 -VNkL4sBF4_-Pm_zjGsE
../../arxiv\astro-ph.updates.on.arXiv.org/001004 -lNkL4sBF4_-Pm_zjGsE
../../arxiv\astro-ph.updates.on.arXiv.org/001005 -1NkL4sBF4_-Pm_zjGsE
../../arxiv\astro-ph.updates.on.arXiv.org/001006 _FNkL4sBF4_-Pm_zjGsE
../../arxiv\astro-ph.updates.on.arXiv.org/001007 _VNkL4sBF4_-Pm_zjGsE
../../arxiv\astro-ph.updates.on.arXiv.org/001008 _lNkL4sBF4_-Pm_zjGsE
../../arxiv\astro-ph.updates.on.arXiv.org/001009 _1NkL4sBF4_-Pm_zjGsE
../../arxiv\astro-ph.updates.on.arXiv.org/001010 AFNkL4sBF4_-Pm_zjGwE
../../arxiv\astro-ph.updates.on.arXiv.org/001011 AVNkL4sBF4_-Pm_zjGwE
../../arxiv\astro-ph.updates.on.arXiv.org/001012 AlNkL4sBF4_-Pm_zjGwE
../../arxiv\astro-ph.updates.on.arXiv.org/001013 A1NkL4sBF4_-Pm_zjGwE
../../arxiv\astro-ph.updates.on.arXiv.org/001014 BFNkL4sBF4_-Pm_zjGwE
../../arxiv\astro-ph

  7%|▋         | 4001/58102 [00:01<00:11, 4693.95it/s]

...

../../arxiv\physics.updates.on.arXiv.org/002822 LlRkL4sBF4_-Pm_z9zPb
../../arxiv\physics.updates.on.arXiv.org/002823 L1RkL4sBF4_-Pm_z9zPb
../../arxiv\physics.updates.on.arXiv.org/002824 MFRkL4sBF4_-Pm_z9zPb
../../arxiv\physics.updates.on.arXiv.org/002825 MVRkL4sBF4_-Pm_z9zPb
../../arxiv\physics.updates.on.arXiv.org/002826 MlRkL4sBF4_-Pm_z9zPb
../../arxiv\physics.updates.on.arXiv.org/002827 M1RkL4sBF4_-Pm_z9zPb
../../arxiv\physics.updates.on.arXiv.org/002828 NFRkL4sBF4_-Pm_z9zPb
../../arxiv\physics.updates.on.arXiv.org/002829 NVRkL4sBF4_-Pm_z9zPb
../../arxiv\physics.updates.on.arXiv.org/002830 NlRkL4sBF4_-Pm_z9zPb
../../arxiv\physics.updates.on.arXiv.org/002831 N1RkL4sBF4_-Pm_z9zPb
../../arxiv\physics.updates.on.arXiv.org/002832 OFRkL4sBF4_-Pm_z9zPb
../../arxiv\physics.updates.on.arXiv.org/002833 OVRkL4sBF4_-Pm_z9zPb
../../arxiv\physics.updates.on.arXiv.org/002834 OlRkL4sBF4_-Pm_z9zPb
../../arxiv\physics.updates.on.arXiv.org/002835 O1RkL4sBF4_-Pm_z9zPb
../../arxiv\physics.updates.on.arX

 97%|█████████▋| 56560/58102 [00:06<00:00, 12349.06it/s]

../../arxiv\physics.updates.on.arXiv.org/005822 5lRkL4sBF4_-Pm_z_D7e
../../arxiv\physics.updates.on.arXiv.org/005823 51RkL4sBF4_-Pm_z_D7e
../../arxiv\physics.updates.on.arXiv.org/005824 6FRkL4sBF4_-Pm_z_D7e
../../arxiv\physics.updates.on.arXiv.org/005825 6VRkL4sBF4_-Pm_z_D7e
../../arxiv\physics.updates.on.arXiv.org/005826 6lRkL4sBF4_-Pm_z_D7e
../../arxiv\physics.updates.on.arXiv.org/005827 61RkL4sBF4_-Pm_z_D7e
../../arxiv\physics.updates.on.arXiv.org/005828 7FRkL4sBF4_-Pm_z_D7e
../../arxiv\physics.updates.on.arXiv.org/005829 7VRkL4sBF4_-Pm_z_D7e
../../arxiv\physics.updates.on.arXiv.org/005830 7lRkL4sBF4_-Pm_z_D7e
../../arxiv\physics.updates.on.arXiv.org/005831 71RkL4sBF4_-Pm_z_D7e
../../arxiv\physics.updates.on.arXiv.org/005832 8FRkL4sBF4_-Pm_z_D7e
../../arxiv\physics.updates.on.arXiv.org/005833 8VRkL4sBF4_-Pm_z_D7e
../../arxiv\physics.updates.on.arXiv.org/005834 8lRkL4sBF4_-Pm_z_D7e
../../arxiv\physics.updates.on.arXiv.org/005835 81RkL4sBF4_-Pm_z_D7e
../../arxiv\physics.updates.on.arX

100%|██████████| 58102/58102 [00:06<00:00, 8360.09it/s] 

../../arxiv\quant-ph.updates.on.arXiv.org/001501 21RlL4sBF4_-Pm_zAUkv
../../arxiv\quant-ph.updates.on.arXiv.org/001502 3FRlL4sBF4_-Pm_zAUkv
../../arxiv\quant-ph.updates.on.arXiv.org/001503 3VRlL4sBF4_-Pm_zAUkv
../../arxiv\quant-ph.updates.on.arXiv.org/001504 3lRlL4sBF4_-Pm_zAUkv
../../arxiv\quant-ph.updates.on.arXiv.org/001505 31RlL4sBF4_-Pm_zAUkv
../../arxiv\quant-ph.updates.on.arXiv.org/001506 4FRlL4sBF4_-Pm_zAUkv
../../arxiv\quant-ph.updates.on.arXiv.org/001507 4VRlL4sBF4_-Pm_zAUkv
../../arxiv\quant-ph.updates.on.arXiv.org/001508 4lRlL4sBF4_-Pm_zAUkv
../../arxiv\quant-ph.updates.on.arXiv.org/001509 41RlL4sBF4_-Pm_zAUkv
../../arxiv\quant-ph.updates.on.arXiv.org/001510 5FRlL4sBF4_-Pm_zAUkv
../../arxiv\quant-ph.updates.on.arXiv.org/001511 5VRlL4sBF4_-Pm_zAUkv
../../arxiv\quant-ph.updates.on.arXiv.org/001512 5lRlL4sBF4_-Pm_zAUkv
../../arxiv\quant-ph.updates.on.arXiv.org/001513 51RlL4sBF4_-Pm_zAUkv
../../arxiv\quant-ph.updates.on.arXiv.org/001514 6FRlL4sBF4_-Pm_zAUkv
../../arxiv\quant-ph

In [3]:
# from elasticsearch.helpers import scan
# from pprint import pprint
# from elasticsearch import Elasticsearch
# import tqdm
# import numpy as np

# # get tf-idf vector from doc (internal) id
# def tf_idf(doc_id):
#     # does nothing, adapt to your needs
#     return []

# # normalizes weights so that resulting vec has length 1
# def normalize(l1):
#     # does nothing, adapt to your needs
#     return l1

# client = Elasticsearch("http://localhost:9200", request_timeout=1000)

# r = 10  # only return r top docs
# query = 'computer magic'
# sims = dict()

# l2query  = np.sqrt(len(query.split()))  # l2 of query assuming 0-1 vector representation

# # get nr. of docs; just for the progress bar
# ndocs = int(client.cat.count(index='arxiv', format = "json")[0]['count'])

# # scan through docs, compute cosine sim between query and each doc
# for s in tqdm.tqdm(scan(client, index='arxiv', query={"query" : {"match_all": {}}}), total=ndocs):
#     docid = s['_source']['path']   # use path as id
    
#     sims[docid] = 0.0
#     weights = dict(normalize(tf_idf(s['_id'])))   # get tf-idf weights representing doc as dict
#     for w in query.split():  # gets terms as a list
#         if w in weights:    # probably need to do something fancier to make sure that word is in vocabulary etc.
#             sims[docid] += weights[w]   # accumulates if w in current doc
#     # normalize sim
#     sims[docid] /= l2query

# # now sort by cosine similarity
# sorted_answer = sorted(sims.items(), key=lambda kv: kv[1], reverse=True)
# pprint(sorted_answer[:r])


100%|██████████| 58102/58102 [05:49<00:00, 166.07it/s]

[('/tmp/arxiv/quant-ph.updates.on.arXiv.org/000650', 0.46298539019176793),
 ('/tmp/arxiv/quant-ph.updates.on.arXiv.org/000677', 0.46285572520081464),
 ('/tmp/arxiv/cond-mat.updates.on.arXiv.org/003482', 0.41693456487012037),
 ('/tmp/arxiv/quant-ph.updates.on.arXiv.org/001475', 0.3078298379878905),
 ('/tmp/arxiv/astro-ph.updates.on.arXiv.org/002083', 0.26997407750109564),
 ('/tmp/arxiv/math.updates.on.arXiv.org/002825', 0.2637693594252774),
 ('/tmp/arxiv/astro-ph.updates.on.arXiv.org/001294', 0.2583918756706909),
 ('/tmp/arxiv/hep-th.updates.on.arXiv.org/000265', 0.2554940223200789),
 ('/tmp/arxiv/math.updates.on.arXiv.org/000955', 0.2554940223200789),
 ('/tmp/arxiv/hep-th.updates.on.arXiv.org/000255', 0.2505494496917682)]


In [24]:
nz = len([x for x, s in sorted_answer if s>0])
total = len(sorted_answer)
print(f'There are {nz} docs with non-zero similarity out of {total}, i.e. {100.0*nz/total:.1f}%')

There are 1948 docs with non-zero similarity out of 58102, i.e. 3.4%


## 3. Your tasks

---

**Exercise 1:**  

Make sure you understand the algorithm for implementing search described in the lecture notes. Both slow and efficient versions. Describe
the number of sums you need to do in both slow and quick versions for the following toy example with a vocabulary of size 4 and four documents:

- $q = 0,1,1,0$

- document-term matrix:
<center>


|        | t1  | t2  | t3  | t4  |
|--------|-----|-----|-----|-----|
| **d1** | 1.2 | 0.0 | 0.0 | 0.0 |
| **d2** | 0.7 | 0.3 | 1.5 | 0.1 |
| **d3** | 0.0 | 0.0 | 0.0 | 0.7 |
| **d4** | 2.0 | 0.0 | 0.0 | 0.0 |

</center>

---

**Exercise 2:**

Implement the quick version; run both slow and quick versions and report times (as a reference, in my old laptop it takes around 5m30s to run the slow version in the code above). Make sure both versions return the same answer. Note that you will need to build an inverted index in order to implement the efficient version as explained in class; it may take time but this is done once for all queries, and can be done "off-line".

---

**Exercise 3:**

Compare the results for a few sample queries that you get from your quick version and ElasticSearch search. Do you get similar results? Which is faster?

---

## 4. Rules of delivery

- To be solved in _pairs_.

- No plagiarism; don't discuss your work with other teams. You can ask for help to others for simple things, such as recalling a python instruction or module, but nothing too specific to the session.

- If you feel you are spending much more time than the rest of the classmates, ask us for help. Questions can be asked either in person or by email, and you'll never be penalized by asking questions, no matter how stupid they look in retrospect.

- Write a short report listing the solutions to the exercises proposed. Include things like the important parts of your implementation (data structures used for representing objects, algorithms used, etc). You are welcome to add conclusions and findings that depart from what we asked you to do. We encourage you to discuss the difficulties you find; this lets us give you help and also improve the lab session for future editions.

- Turn the report to PDF. Make sure it has your names, date, and title. Include your code in your submission.

- Submit your work through the [raco](http://www.fib.upc.edu/en/serveis/raco.html) _before November 6th, 2023_.